In [67]:
import os
from datetime import datetime
import pandas as pd
import numpy as np
import itertools

import dash
import dash_core_components as dcc
import dash_html_components as html
from dash.dependencies import Input, Output
from dash.exceptions import PreventUpdate
import plotly.graph_objects as go
from plotly.colors import n_colors
import plotly.express as px

In [68]:
INPUT_DIR = "../output-data/"
parse_dates = ['date']  # need the correct format
trends_df = pd.read_csv(INPUT_DIR + 'transformed-google-trends.csv', parse_dates=parse_dates)
#trends_df = trends_df[trends_df.score_difference.notna()]
#trends_df["score_difference"] = trends_df["score_difference"].astype("int")

# positive_trends_df = trends_df[trends_df["score_difference"] >= 0 ]
# negative_trends_df = trends_df[trends_df["score_difference"] <= 0 ]
#trends_df = 

In [69]:
columns = trends_df.columns
trends_df.head()

date  score country    term translated_term  score_difference  \
0 2019-11-03     38     ger  baking          backen                 2   
1 2019-11-10     42     ger  baking          backen                 6   
2 2019-11-17     44     ger  baking          backen                 5   
3 2019-11-24     46     ger  baking          backen                 5   
4 2019-12-01     48     ger  baking          backen                 6   

     date_str display_term renamed_term  iso_num iso_alpha score_diff_positive  
0  2019-11-03       baking       baking    276.0       DEU            positive  
1  2019-11-10       baking       baking    276.0       DEU            positive  
2  2019-11-17       baking       baking    276.0       DEU            positive  
3  2019-11-24       baking       baking    276.0       DEU            positive  
4  2019-12-01       baking       baking    276.0       DEU            positive

In [70]:
df = pd.read_csv("https://raw.githubusercontent.com/plotly/datasets/master/violin_data.csv")

fig = go.Figure()

fig.add_trace(go.Violin(x=df['day'][ df['smoker'] == 'Yes' ],
                        y=df['total_bill'][ df['smoker'] == 'Yes' ],
                        legendgroup='Yes', scalegroup='Yes', name='Yes',
                        side='negative',
                        line_color='blue')
             )
fig.add_trace(go.Violin(x=df['day'][ df['smoker'] == 'No' ],
                        y=df['total_bill'][ df['smoker'] == 'No' ],
                        legendgroup='No', scalegroup='No', name='No',
                        side='positive',
                        line_color='orange')
             )
fig.update_traces(meanline_visible=True)
fig.update_layout(violingap=0, violinmode='overlay')
fig.show()

In [71]:
def make_ridgeline_distribution(row, keep_col, multiplier_col): 
    """Take a row of a dataframe and return a list with column multipl"""
    return list(np.full((row[multiplier_col],len(row.index)), row))

In [73]:
ridgeline_array = trends_df.apply(lambda x: make_ridgeline_distribution(x, "date", "score_difference"), axis=1).tolist()
ridgeline_df = pd.DataFrame(list(itertools.chain.from_iterable(ridgeline_array)), columns=columns)

In [77]:
df = pd.read_csv("https://raw.githubusercontent.com/plotly/datasets/master/violin_data.csv")

fig = go.Figure()

fig.add_trace(go.Violin(x=ridgeline_df[ridgeline_df.score_diff_positive == "positive"]['term'],
                        y=ridgeline_df['date'],
                        legendgroup='Yes', scalegroup='Yes', name='Yes',
                        side='positive',
                        line_color='blue')
             )
fig.add_trace(go.Violin(x=ridgeline_df[ridgeline_df.score_diff_positive == "negative"]['term'],
                        y=ridgeline_df['date'],
                        legendgroup='No', scalegroup='No', name='No',
                        side='negative',
                        line_color='blue')
             )

fig.update_traces(orientation='h', side='positive', width=3, points=False)

In [96]:
selected_country_df = ridgeline_df

# JOY MAP
num_categories = selected_country_df.renamed_term.nunique()
colors = n_colors('rgb(5, 200, 200)', 'rgb(200, 10, 10)', num_categories, colortype='rgb')
joy_fig = go.Figure()

# TODO: modify so that its zipping together trends_df filtered on item type for each color
for renamed_term, color in zip(selected_country_df.renamed_term.unique(), colors):
    joy_filtered_data = selected_country_df[(selected_country_df.renamed_term == renamed_term) & (selected_country_df.score_diff_positive == "positive")]  # show one term at a time

    joy_fig.add_trace(go.Violin(x=joy_filtered_data["date"],
                                line_color=color,
                                name=renamed_term,
                                customdata=["date_str"],
                                hoverinfo="skip"
                                )
                      )
joy_fig.update_traces(orientation='h', side='positive', width=3, points=False)


# Joy Fig Negative 
joy_fig_neg = go.Figure()
for renamed_term, color in zip(selected_country_df.renamed_term.unique(), colors):
    joy_filtered_data = selected_country_df[(selected_country_df.renamed_term == renamed_term) & (selected_country_df.score_diff_positive == "negative")]  # show one term at a time

    joy_fig_neg.add_trace(go.Violin(x=joy_filtered_data["date"],
                                line_color=color,
                                name=renamed_term,
                                customdata=["date_str"],
                                hoverinfo="skip"
                                )
                      )
joy_fig_neg.update_traces(orientation='h', side='negative', width=3, points=False)

# Combine positive and negative joy figs
for i in range(len(joy_fig_neg.data)):
    joy_fig.add_trace(joy_fig_neg.data[i])

# joy_fig.update_layout(xaxis_showgrid=False, xaxis_zeroline=False, showlegend=False)
# joy_fig.update_xaxes(showticklabels=False, title="November 2019 through October 2020")
joy_fig.update_layout(height=1000)

joy_fig.show()

In [87]:
joy_fig_neg.data[14]

Violin({
    'customdata': [date_str],
    'hoverinfo': 'skip',
    'line': {'color': 'rgb(200.0, 10.0, 10.0)'},
    'name': 'toilet paper',
    'orientation': 'h',
    'points': False,
    'side': 'negative',
    'width': 3,
    'x': array([datetime.datetime(2019, 11, 24, 0, 0),
                datetime.datetime(2019, 12, 22, 0, 0),
                datetime.datetime(2020, 1, 5, 0, 0),
                datetime.datetime(2020, 1, 5, 0, 0),
                datetime.datetime(2020, 1, 5, 0, 0),
                datetime.datetime(2020, 1, 12, 0, 0),
                datetime.datetime(2020, 1, 12, 0, 0),
                datetime.datetime(2020, 1, 26, 0, 0),
                datetime.datetime(2020, 2, 2, 0, 0),
                datetime.datetime(2020, 8, 16, 0, 0),
                datetime.datetime(2019, 11, 3, 0, 0),
                datetime.datetime(2019, 11, 17, 0, 0),
                datetime.datetime(2019, 12, 1, 0, 0),
                datetime.datetime(2019, 12, 15, 0, 0),
                da

In [79]:
import plotly.graph_objects as go
from plotly.colors import n_colors
import numpy as np
np.random.seed(1)

# 12 sets of normal distributed random data, with increasing mean and standard deviation
data = (np.linspace(1, 2, 12)[:, np.newaxis] * np.random.randn(12, 200) +
            (np.arange(12) + 2 * np.random.random(12))[:, np.newaxis])

colors = n_colors('rgb(5, 200, 200)', 'rgb(200, 10, 10)', 12, colortype='rgb')

fig = go.Figure()
for data_line, color in zip(data, colors):
    fig.add_trace(go.Violin(x=data_line, line_color=color))

    
    
fig.update_traces(orientation='h', side='negative', width=3, points=False)
fig.update_layout(xaxis_showgrid=False, xaxis_zeroline=False)
fig.show()

In [28]:
df[df['smoker']=='Yes']['day']

56     Sat
58     Sat
60     Sat
61     Sat
62     Sat
      ... 
234    Sat
236    Sat
237    Sat
240    Sat
241    Sat
Name: day, Length: 93, dtype: object